In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

# from utils import download_para, retrieve_landings18, retrieve_toffs18
from traffic.data import airports, opensky
from traffic.core import Traffic
from tqdm.auto import tqdm

/Users/figu/Documents/git/OSN23-RET/.venv/lib/python3.11/site-packages/pyopensky/impala.py:17: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


## Download OSN data


In [2]:
start = "2019-10"
stop = "2019-11"
trajs_before = (
    opensky.history(
        start,
        stop,
        bounds=airports["LPPT"].shape.convex_hull.buffer(0.3),
    )
    .assign_id()
    .eval()
)

In [3]:
start = "2022-12"
stop = "2023-01"
trajs_after = (
    opensky.history(
        start,
        stop,
        bounds=airports["LPPT"].shape.convex_hull.buffer(0.3),
    )
    .assign_id()
    .eval()
)
trajs_before | trajs_after

we remove some noise in the data:


In [4]:
trajs_before.data = trajs_before.data.drop_duplicates(
    subset=["flight_id", "last_position"]
)
trajs_after.data = trajs_after.data.drop_duplicates(
    subset=["flight_id", "last_position"]
)

### Identification of trajectory phases

We use very simple classification, it will be refined once we check the landings runway 20 and toffs runway 20


In [5]:
ids_landings_before = (
    trajs_before.airborne()
    .query("altitude < 4000")
    .summary(["flight_id", "vertical_rate_median"])
    .eval()
    .query("vertical_rate_median<100")
    .flight_id.unique()
)
ids_landings_after = (
    trajs_after.airborne()
    .query("altitude < 4000")
    .summary(["flight_id", "vertical_rate_median"])
    .eval()
    .query("vertical_rate_median<100")
    .flight_id.unique()
)

ids_toffs_before = (
    trajs_before.airborne()
    .query("altitude < 4000")
    .summary(["flight_id", "vertical_rate_median"])
    .eval()
    .query("vertical_rate_median>500")
    .flight_id.unique()
)
ids_toffs_after = (
    trajs_after.airborne()
    .query("altitude < 4000")
    .summary(["flight_id", "vertical_rate_median"])
    .eval()
    .query("vertical_rate_median>500")
    .flight_id.unique()
)

/Users/figu/Documents/git/OSN23-RET/.venv/lib/python3.11/site-packages/numpy/lib/nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/Users/figu/Documents/git/OSN23-RET/.venv/lib/python3.11/site-packages/numpy/lib/nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/Users/figu/Documents/git/OSN23-RET/.venv/lib/python3.11/site-packages/numpy/lib/nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/Users/figu/Documents/git/OSN23-RET/.venv/lib/python3.11/site-packages/numpy/lib/nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/Users/figu/Documents/git/OSN23-RET/.venv/lib/python3.11/site-packages/numpy/lib/nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/Users/figu/Document

we only keep the airborne part and what's below 4000ft:


In [6]:
toffs_before = trajs_before[ids_toffs_before].airborne().query("geoaltitude < 4000")
landings_before = (
    trajs_before[ids_landings_before].airborne().query("geoaltitude < 4000")
)
toffs_after = trajs_after[ids_toffs_after].airborne().query("geoaltitude < 4000")
landings_after = trajs_after[ids_landings_after].airborne().query("geoaltitude < 4000")
toffs_before | landings_before | toffs_after | landings_after

### Focus on landings

We try to identify landings on rwy 20


In [7]:
def keep_ils(flight):
    return next(flight.aligned_on_ils("LPPT", min_duration="30s"), None)


aligned_before = (
    trajs_before[ids_landings_before]
    .iterate_lazy()
    .pipe(keep_ils)
    .eval(max_workers=1)
)
aligned_after = (
    trajs_after[ids_landings_after].iterate_lazy().pipe(keep_ils).eval(max_workers=1)
)

/Users/figu/Documents/git/OSN23-RET/.venv/lib/python3.11/site-packages/pyproj/geod.py:404: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  return self._inv_point(
/Users/figu/Documents/git/OSN23-RET/.venv/lib/python3.11/site-packages/pyproj/geod.py:404: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  return self._inv_point(
/Users/figu/Documents/git/OSN23-RET/.venv/lib/python3.11/site-packages/pyproj/geod.py:404: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  return sel

In [8]:
landings20_before = aligned_before.query("ILS=='20'")
landings20_after = aligned_after.query("ILS=='20'")
landings20_before | landings20_after

### Unfortunately, especially in 2019, the coverage is not that good and we don't have landings until the threshold so we need to train a ML model that predicts the remaining time2fly


In [9]:
ids_full_landing = landings20_after.query("distance<0.03").data.flight_id.unique()
full_landings20 = landings20_after[ids_full_landing]


def add_time2fly(flight):
    flight.data["time2fly"] = (flight.stop - flight.data.timestamp).dt.total_seconds()
    flight.data["typecode"] = flight.typecode
    return flight


def add_typecode(flight):
    flight.data["typecode"] = flight.typecode
    return flight


full_landings20 = (
    full_landings20.iterate_lazy().pipe(add_time2fly).eval(desc="time2fly")
)
landings20_after = (
    landings20_after.iterate_lazy().pipe(add_typecode).eval(desc="typecode")
)
landings20_before = (
    landings20_before.iterate_lazy().pipe(add_typecode).eval(desc="typecode")
)

Output()

Output()

Output()

In [10]:
fig = go.Figure()
fig.add_trace(
    go.Histogram(
        x=landings20_before.summary(["distance_min"]).eval()["distance_min"],
        name="Oct 2019",

    )
)
fig.add_trace(
    go.Histogram(
        x=landings20_after.summary(["distance_min"]).eval()["distance_min"],
        name="Dec 2022",
    )
)
width = 800
height = 500

fig.update_layout(
    width=width,
    height=height,
    # title_text="Minimum observed distance from runway threshold for landings in 2019",
    xaxis_title_text="Distance from runway threshold [NM]",
    yaxis_title_text="Count",
    xaxis_range=[0, 11],
    # make legend horizontal on top right above the plot
    legend=dict(yanchor="top", y=1.1, xanchor="right", x=1, orientation="h"),
    barmode="overlay",
)
# reduce opacity to see both histograms
fig.update_traces(opacity=0.75)
fig.write_image("figures/d_from_rway_lnds.pdf")
fig.show()

/Users/figu/Documents/git/OSN23-RET/.venv/lib/python3.11/site-packages/kaleido/scopes/base.py:188: DeprecationWarning:

setDaemon() is deprecated, set the daemon attribute instead



#### Model training


In [11]:
from xgboost import XGBRegressor
from sklearn.model_selection import train_test_split

# create X_train, X_val, X_test, y_train, y_val, y_test
df = full_landings20.data.query("distance<12")
df = df.reset_index()
df["typecode"] = df.typecode.astype("category")
X = df[["distance", "typecode", "groundspeed", "geoaltitude", "track", "vertical_rate"]]
y = df.time2fly
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.4, random_state=42
)
X_test, X_val, y_test, y_val = train_test_split(
    X_test, y_test, test_size=0.5, random_state=42
)

# train the model with early stopping using X_train, y_train, X_val, y_val
model = XGBRegressor(
    enable_categorical=True,
    n_estimators=100000,
    learning_rate=0.05,
    max_depth=4,
    random_state=42,
    objective="reg:squarederror",
)
model.fit(
    X_train, y_train, early_stopping_rounds=50, eval_set=[(X_val, y_val)], verbose=1
)

# evaluate the model using X_test, y_test
from sklearn.metrics import mean_squared_error

y_pred = model.predict(X_test)
rmse = mean_squared_error(y_test, y_pred, squared=True)
print(f"RMSE: {rmse}")

df_pred = df.loc[X_test.index]
df_pred["pred"] = y_pred
df_pred["error"] = df_pred.time2fly - df_pred.pred

[0]	validation_0-rmse:77.33795
[1]	validation_0-rmse:73.62092
[2]	validation_0-rmse:70.09638
[3]	validation_0-rmse:66.74573
[4]	validation_0-rmse:63.56682
[5]	validation_0-rmse:60.54404
[6]	validation_0-rmse:57.68615
[7]	validation_0-rmse:54.96398
[8]	validation_0-rmse:52.39440
[9]	validation_0-rmse:49.94019
[10]	validation_0-rmse:47.62835
[11]	validation_0-rmse:45.42288
[12]	validation_0-rmse:43.34456
[13]	validation_0-rmse:41.36908
[14]	validation_0-rmse:39.49149
[15]	validation_0-rmse:37.71291
[16]	validation_0-rmse:36.03664
[17]	validation_0-rmse:34.44240
[18]	validation_0-rmse:32.93239
[19]	validation_0-rmse:31.50107
[20]	validation_0-rmse:30.14179
[21]	validation_0-rmse:28.86377
[22]	validation_0-rmse:27.64079
[23]	validation_0-rmse:26.48926
[24]	validation_0-rmse:25.39599
[25]	validation_0-rmse:24.36796
[26]	validation_0-rmse:23.39238
[27]	validation_0-rmse:22.47003
[28]	validation_0-rmse:21.60386
[29]	validation_0-rmse:20.78071
[30]	validation_0-rmse:20.00828
[31]	validation_0-

In [12]:
# prediction error check
fig = px.histogram(
    y_pred - y_test,
    histnorm="probability density",
)
fig.update_layout(
    width=800,
    height=500,
    xaxis_title_text="landing time prediction error [s]",
    showlegend=False,
)
fig.write_image("figures/time2fly_prediction_error.pdf")

In [13]:
fig = px.scatter(df_pred, x="distance", y="pred", color="error")
fig.update_layout(
    width=800,
    height=500,
    xaxis_title_text="distance from runway threshold [NM]",
    yaxis_title_text="Time to fly prediction [s]",
    showlegend=False,
    coloraxis_colorbar=dict(
        title="error [s]",
    ),
)
fig.write_image("figures/time2fly_prediction_error_distance.pdf")
fig.show()
# rename colorbar to prediction error[s]

In [14]:
# model inference
landings20_before = landings20_before.last("1S").eval()
landings20_before.data["typecode"] = landings20_before.data.typecode.astype("category")
landings20_before.data["time2fly"] = model.predict(
    landings20_before.data[
        ["distance", "typecode", "groundspeed", "geoaltitude", "track", "vertical_rate"]
    ]
)
landings20_before.data["t"] = landings20_before.data["timestamp"] + pd.to_timedelta(
    landings20_before.data["time2fly"], unit="s"
)

landings20_after = landings20_after.last("1S").eval()
landings20_after.data["typecode"] = landings20_after.data.typecode.astype("category")
landings20_after.data["time2fly"] = model.predict(
    landings20_after.data[
        ["distance", "typecode", "groundspeed", "geoaltitude", "track", "vertical_rate"]
    ]
)
landings20_after.data["t"] = landings20_after.data["timestamp"] + pd.to_timedelta(
    landings20_after.data["time2fly"], unit="s"
)

### Focus on toffs


Here it's pretty stupid, we just draw a box at the end of runway 20 to identify toffs 20


In [15]:
from datetime import timedelta

bbox = (-9.2, 38.6, -9.1, 38.76)
duration_min = timedelta(seconds=30)
ids20 = [
    f.flight_id for f in toffs_before.inside_bbox(bbox) if f.duration > duration_min
]
toffs20_before = toffs_before[ids20]
ids20 = [
    f.flight_id for f in toffs_after.inside_bbox(bbox) if f.duration > duration_min
]
toffs20_after = toffs_after[ids20]
toffs20_before | toffs20_after

In [16]:
toffs20_before = toffs20_before.iterate_lazy().pipe(add_typecode).eval(desc="typecode")
toffs20_after = toffs20_after.iterate_lazy().pipe(add_typecode).eval(desc="typecode")

Output()

Output()

In [17]:
subset_after = toffs_after[toffs20_after.data.flight_id.unique()].sample(100).first('3T').eval()
subset_before = toffs_before[toffs20_before.data.flight_id.unique()].sample(100).first('3T').eval()


fig = go.Figure(go.Scattermapbox())
for i, f in enumerate(subset_after):
    fig.add_trace(
        go.Scattermapbox(
            lat=f.data.latitude,
            lon=f.data.longitude,
            mode="lines",
            line=dict(width=1, color="red"),
            name='Departure RWY20 after RET',
            showlegend=i<1,
        )
    )

for i, f in enumerate(subset_before):
    fig.add_trace(
        go.Scattermapbox(
            lat=f.data.latitude,
            lon=f.data.longitude,
            mode="lines",
            line=dict(width=1, color="blue"),
            name='Departure RWY20 before RET',
            showlegend=i<1,
        )
    )

fig.add_trace(
    go.Scattermapbox(
        lat=[bbox[1], bbox[1], bbox[3], bbox[3], bbox[1]],
        lon=[bbox[0], bbox[2], bbox[2], bbox[0], bbox[0]],
        mode="lines",
        line=dict(width=1, color="black"),
        name='Virtual Box',
        showlegend=True,
    )
)


subset_after = landings_after[landings20_after.data.flight_id.unique()].sample(100).last('3T').eval()
subset_before = landings_before[landings20_before.data.flight_id.unique()].sample(100).last('3T').eval()

for i, f in enumerate(subset_after):
    fig.add_trace(
        go.Scattermapbox(
            lat=f.data.latitude,
            lon=f.data.longitude,
            mode="lines",
            line=dict(width=1, color="darkred"),
            name='Arrivals RWY20 after RET',
            showlegend=i<1,
        )
    )

for i, f in enumerate(subset_before):
    fig.add_trace(
        go.Scattermapbox(
            lat=f.data.latitude,
            lon=f.data.longitude,
            mode="lines",
            line=dict(width=1, color="darkblue"),
            name='Arrivals RWY20 before RET',
            showlegend=i<1,
        )
    )




fig.update_layout(
    mapbox_style="carto-positron",
    mapbox_zoom=9.4,
    mapbox_center={"lat": 38.79, "lon": -9.13},
    height=500,
    width=700,
    margin={"r": 0, "t": 0, "l": 0, "b": 0},
)

fig.show()
fig.write_image("figures/sample_arrivals_departures_on_map.pdf")

# Estimation of the already flown time using Gradient Boosting

##### We want to TOFFS to start at the end of runway (or as close as possible)


In [18]:
threshold = airports["LPPT"].runways.list[0]
toffs20_after = toffs20_after.distance(threshold).eval(desc="distance")
toffs20_before = toffs20_before.distance(threshold).eval(desc="distance")

Output()

Output()

In [19]:
fig = go.Figure()
fig.add_trace(
    go.Histogram(
        x=toffs20_before.summary(["distance_min"]).eval()["distance_min"],
        name="Oct 2019",
        # nbinsx=50,
        # marker_color="rgb(158,202,225)",
    )
)
fig.add_trace(
    go.Histogram(
        x=toffs20_after.summary(["distance_min"]).eval()["distance_min"],
        name="Dec 2022",
        # nbinsx=50,
        # marker_color="rgb(158,202,225)",
    )
)
width = 800
height = 500

fig.update_layout(
    width=width,
    height=height,
    # title_text="Minimum observed distance from runway threshold for landings in 2019",
    xaxis_title_text="Distance from runway threshold [NM]",
    yaxis_title_text="Count",
    xaxis_range=[0, 2],
    # make legend horizontal on top right above the plot
    legend=dict(yanchor="top", y=1.1, xanchor="right", x=1, orientation="h"),
    barmode="overlay",
)
# reduce opacity to see both histograms
fig.update_traces(opacity=0.75)
fig.write_image("figures/d_from_rway_toffs.pdf")
fig.show()

In [20]:
def keep_after_threshold(flight):
    # find index where distance is minimum
    idx = flight.data.distance.idxmin()
    # keep data after idx
    flight.data = flight.data.loc[idx:]
    flight.data = flight.data.assign(
        seconds_since_toff=lambda df: (
            df.timestamp - df.timestamp.min()
        ).dt.total_seconds()
    )
    flight.data["typecode"] = flight.typecode
    return flight


toffs20_after = (
    toffs20_after.iterate_lazy()
    .pipe(keep_after_threshold)
    .eval(desc="keep_after_threshold")
)
toffs20_after

Output()

flight_id  count
0    BBO101_144    296
1    BBO101_136    266
2    BBO101_138    222
3    BBO101_225    187
4  DTA651_17145    181
5  DTA651_17139    176
6  TAP117_12425    170
7  DTA651_17144    167
8  DTA651_17142    166
9    SWT132_624    166

To train ML model we need to have a sample very close to threshold


In [21]:
ids_threshold = toffs20_after.query("distance<0.03").data.flight_id.unique()
toffs20_after_threshold = toffs20_after[ids_threshold]
toffs20_after_threshold

flight_id  count
0    BBO101_144    296
1  DTA651_17145    181
2  DTA651_17139    176
3  TAP117_12425    170
4  DTA651_17142    166
5    SWT132_624    166
6  DTA651_16479    164
7    SWT132_620    158
8    SWT130_606    151
9  TAP023_12459    150

#### Model training


In [22]:
from xgboost import XGBRegressor
from sklearn.model_selection import train_test_split

# create X_train, X_val, X_test, y_train, y_val, y_test
df = toffs20_after_threshold.data.query("distance<3")


df["typecode"] = df.typecode.astype("category")
df = df.reset_index()
X = df[["distance", "typecode", "groundspeed", "geoaltitude", "track"]]
y = df.seconds_since_toff
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.4, random_state=1)
X_test, X_val, y_test, y_val = train_test_split(
    X_test, y_test, test_size=0.5, random_state=1
)

# train the model with early stopping using X_train, y_train, X_val, y_val
model = XGBRegressor(
    enable_categorical=True,
    n_estimators=10000,
    learning_rate=0.05,
    max_depth=4,
    random_state=1,
    objective="reg:squarederror",
)
model.fit(
    X_train, y_train, early_stopping_rounds=50, eval_set=[(X_val, y_val)], verbose=1
)

# evaluate the model using X_test, y_test
from sklearn.metrics import mean_squared_error

y_pred = model.predict(X_test)
mse = mean_squared_error(y_test, y_pred)
print(f"MSE: {mse}")

df_pred = df.loc[X_test.index]
df_pred["pred"] = y_pred
df_pred["error"] = df_pred.seconds_since_toff - df_pred.pred

[0]	validation_0-rmse:18.06872
[1]	validation_0-rmse:17.19379
[2]	validation_0-rmse:16.36274
[3]	validation_0-rmse:15.57381
[4]	validation_0-rmse:14.82471
[5]	validation_0-rmse:14.11343
[6]	validation_0-rmse:13.43932
[7]	validation_0-rmse:12.79916
[8]	validation_0-rmse:12.19275


/var/folders/hs/m903817s4cq4rdmprtgnm4dm0000gq/T/ipykernel_78170/43769440.py:8: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



[9]	validation_0-rmse:11.61730
[10]	validation_0-rmse:11.07061
[11]	validation_0-rmse:10.55306
[12]	validation_0-rmse:10.06117
[13]	validation_0-rmse:9.59554
[14]	validation_0-rmse:9.15285
[15]	validation_0-rmse:8.73453
[16]	validation_0-rmse:8.33702
[17]	validation_0-rmse:7.96075
[18]	validation_0-rmse:7.60335
[19]	validation_0-rmse:7.26561
[20]	validation_0-rmse:6.94571
[21]	validation_0-rmse:6.64344
[22]	validation_0-rmse:6.35572
[23]	validation_0-rmse:6.08269
[24]	validation_0-rmse:5.82657
[25]	validation_0-rmse:5.58293
[26]	validation_0-rmse:5.35267
[27]	validation_0-rmse:5.13630
[28]	validation_0-rmse:4.93043
[29]	validation_0-rmse:4.73612
[30]	validation_0-rmse:4.55282
[31]	validation_0-rmse:4.37923
[32]	validation_0-rmse:4.21625
[33]	validation_0-rmse:4.06203
[34]	validation_0-rmse:3.91696
[35]	validation_0-rmse:3.77943
[36]	validation_0-rmse:3.65097
[37]	validation_0-rmse:3.52855
[38]	validation_0-rmse:3.41277
[39]	validation_0-rmse:3.30538
[40]	validation_0-rmse:3.20333
[41]	

In [23]:
fig = px.histogram(y_pred - y_test)
fig.update_layout(
    width=800,
    height=500,
    xaxis_title_text="take-off time prediction error [s]",
    showlegend=False,
)
fig.write_image("figures/toff_prediction_error.pdf")

#### Model inference


In [24]:
toffs20_before = toffs20_before.first("1S").eval()
toffs20_before.data["typecode"] = toffs20_before.data.typecode.astype("category")
toffs20_before.data["seconds_since_toff"] = model.predict(
    toffs20_before.data[["distance", "typecode", "groundspeed", "geoaltitude", "track"]]
)
toffs20_before.data["t"] = toffs20_before.data["timestamp"] - pd.to_timedelta(
    toffs20_before.data["seconds_since_toff"], unit="s"
)

toffs20_after = toffs20_after.first("1S").eval()
toffs20_after.data["typecode"] = toffs20_after.data.typecode.astype("category")
toffs20_after.data["seconds_since_toff"] = model.predict(
    toffs20_after.data[["distance", "typecode", "groundspeed", "geoaltitude", "track"]]
)
toffs20_after.data["t"] = toffs20_after.data["timestamp"] - pd.to_timedelta(
    toffs20_after.data["seconds_since_toff"], unit="s"
)

In [25]:
t_since_dep_before = toffs20_before.data.seconds_since_toff
t_since_dep_after = toffs20_after.data.seconds_since_toff
fig = go.Figure()
fig.add_trace(go.Histogram(x=t_since_dep_before, name="before"))
fig.add_trace(go.Histogram(x=t_since_dep_after, name="after"))
fig.update_layout(barmode="overlay")
fig.update_traces(opacity=0.75)
fig.show()

In [26]:
toffs20_before.data["t"] = toffs20_before.data["timestamp"] - toffs20_before.data[
    "seconds_since_toff"
].apply(lambda t: timedelta(seconds=t))
toffs20_after.data["t"] = toffs20_after.data["timestamp"] - toffs20_after.data[
    "seconds_since_toff"
].apply(lambda t: timedelta(seconds=t))

In [27]:
landings20_before.data["SRC"] = "ARR"
landings20_after.data["SRC"] = "ARR"
toffs20_before.data["SRC"] = "DEP"
toffs20_after.data["SRC"] = "DEP"
before = landings20_before + toffs20_before
after = landings20_after + toffs20_after
before.data[["t", "SRC"]]

t  SRC
23953 2019-10-14 09:23:58.134582520+00:00  ARR
21382 2019-10-17 09:23:53.870971680+00:00  ARR
35702 2019-10-14 08:37:08.681289673+00:00  ARR
29088 2019-10-24 08:24:22.293731689+00:00  ARR
19972 2019-10-18 08:30:55.743728638+00:00  ARR
...                                   ...  ...
28165    2019-10-28 16:10:54.535158+00:00  DEP
41165    2019-10-30 22:01:47.517279+00:00  DEP
42633    2019-10-12 21:35:56.527232+00:00  DEP
40598    2019-10-15 22:13:21.214096+00:00  DEP
48425    2019-10-17 10:30:16.907553+00:00  DEP

[7545 rows x 2 columns]

In [28]:
count_15min_before = (
    before.data[["t", "SRC"]]
    .set_index("t")
    .sort_index()
    .groupby([pd.Grouper(freq="15min"), "SRC"])
    .size()
    .unstack()
    .fillna(0)
)
count_15min_before.columns = ["n_dep", "n_arr"]
count_15min_before["n_movements"] = (
    count_15min_before["n_dep"] + count_15min_before["n_arr"]
)

count_15min_after = (
    after.data[["t", "SRC"]]
    .set_index("t")
    .sort_index()
    .groupby([pd.Grouper(freq="15min"), "SRC"])
    .size()
    .unstack()
    .fillna(0)
)
count_15min_after.columns = ["n_dep", "n_arr"]
count_15min_after["n_movements"] = (
    count_15min_after["n_dep"] + count_15min_after["n_arr"]
)

In [29]:
q = 0.925
envelope19 = count_15min_before.groupby("n_arr").quantile(q)["n_dep"]
envelope22 = count_15min_after.groupby("n_arr").quantile(q)["n_dep"]
# merge the two dataframes
envelope = pd.merge(
    envelope19, envelope22, left_index=True, right_index=True, suffixes=("_19", "_22")
)
envelope

n_dep_19  n_dep_22
n_arr                    
0.0         5.0       4.0
1.0         5.0       5.0
2.0         5.0       5.0
3.0         5.0       6.0
4.0         5.0       5.0
5.0         5.0       6.0
6.0         5.0       5.0
7.0         2.0       3.0
8.0         1.0       1.0

In [30]:
import numpy as np
import plotly.graph_objs as go
from scipy.optimize import minimize


def piecewise_linear(x, y0, k0, k1, k2, k3, k4, k5, k6, k7):
    x0, x1, x2, x3, x4, x5, x6, x7 = 0, 1, 2, 3, 4, 5, 6, 7

    return np.piecewise(
        x,
        [
            x < x0,
            (x >= x0) & (x < x1),
            (x >= x1) & (x < x2),
            (x >= x2) & (x < x3),
            (x >= x3) & (x < x4),
            (x >= x4) & (x < x5),
            (x >= x5) & (x < x6),
            (x >= x6) & (x < x7),
            x >= x7,
        ],
        [
            lambda x: y0,
            lambda x: k0 * (x - x0) + y0,
            lambda x: k1 * (x - x1) + k0 * (x1 - x0) + y0,
            lambda x: k2 * (x - x2) + k1 * (x2 - x1) + k0 * (x1 - x0) + y0,
            lambda x: k3 * (x - x3)
            + k2 * (x3 - x2)
            + k1 * (x2 - x1)
            + k0 * (x1 - x0)
            + y0,
            lambda x: k4 * (x - x4)
            + k3 * (x4 - x3)
            + k2 * (x3 - x2)
            + k1 * (x2 - x1)
            + k0 * (x1 - x0)
            + y0,
            lambda x: k5 * (x - x5)
            + k4 * (x5 - x4)
            + k3 * (x4 - x3)
            + k2 * (x3 - x2)
            + k1 * (x2 - x1)
            + k0 * (x1 - x0)
            + y0,
            lambda x: k6 * (x - x6)
            + k5 * (x6 - x5)
            + k4 * (x5 - x4)
            + k3 * (x4 - x3)
            + k2 * (x3 - x2)
            + k1 * (x2 - x1)
            + k0 * (x1 - x0)
            + y0,
            lambda x: k7 * (x - x7)
            + k6 * (x7 - x6)
            + k5 * (x6 - x5)
            + k4 * (x5 - x4)
            + k3 * (x4 - x3)
            + k2 * (x3 - x2)
            + k1 * (x2 - x1)
            + k0 * (x1 - x0)
            + y0,
        ],
    )


def func(params, *args):
    x = args[0]
    y = args[1]
    pred = piecewise_linear(x, *params)
    return np.mean((y - pred) ** 2)

In [31]:
x22 = envelope22.index
y22 = envelope22.values
p22 = np.array(
    [y22[0]] + np.diff(y22).clip(-np.inf, 0).tolist()
)  # an example initial guess

x19 = envelope19.index
y19 = envelope19.values
p19 = np.array(
    [y19[0]] + np.diff(y19).clip(-np.inf, 0).tolist()
)  # an example initial guess

p0 = np.array([5.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, -1.0, -2.0])

constraints = [
    {"type": "ineq", "fun": lambda k: (k[i] - k[i + 1])} for i in range(1, len(p0) - 1)
]

bounds = [(0, np.inf)] + [(-np.inf, 0)] * 8
res19 = minimize(
    func,
    p0,
    args=(x19, y19),
    bounds=bounds,
    method="SLSQP",
    constraints=constraints,
)
res22 = minimize(
    func,
    p0,
    args=(x22, y22),
    bounds=bounds,
    method="SLSQP",
    constraints=constraints,
)


fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=x19,
        y=y19,
        name=f"Pre-RET (Oct 2019) P{q*100}",
        mode="markers",
        marker_color="blue",
        marker_symbol="square-open",
        legendgroup="Pre-RET (Oct 2019)"
    )
)
fig.add_trace(
    go.Scatter(
        x=x22,
        y=y22,
        name=f"Post-RET (Dec 2022) P{q*100}",
        mode="markers",
        marker_color="red",
        marker_symbol="cross",
        legendgroup="Post-RET (Dec 2022)",
    )
)
fig.add_trace(
    go.Scatter(
        x=x19,
        y=piecewise_linear(x19, *res19.x),
        name="Pre-RET (Oct 2019) envelope",
        mode="lines",
        line_color="blue",
        legendgroup="Pre-RET (Oct 2019)"
    )
)
fig.add_trace(
    go.Scatter(
        x=x22,
        y=piecewise_linear(x22, *res22.x),
        name="Post-RET (Dec 2022) envelope",
        mode="lines",
        line_color="red",
        legendgroup="Post-RET (Dec 2022)",
    )
)
fig.update_layout(
    height=500,
    width=800,
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1),
    xaxis_range=[0, 8.5],
    yaxis_range=[0, 6.2],
    xaxis_title_text="Number of arrivals per 15min intervals",
    yaxis_title_text="Number of departures per 15min intervals",
)
fig.write_image("figures/envelopes.pdf")
fig.show()

## Density


In [32]:
density19 = count_15min_before.groupby(["n_dep", "n_arr"]).size().unstack(fill_value=0)
density19 = density19 / density19.sum().sum()
density19 = density19.replace(0, np.nan)
density22 = count_15min_after.groupby(["n_dep", "n_arr"]).size().unstack(fill_value=0)
density22 = density22 / density22.sum().sum()
density22 = density22.replace(0, np.nan)

In [33]:
# plot density19 and density23 side by side with the same color scale using plotly subplots
from plotly.subplots import make_subplots

n_lnds_max = np.max((density19.columns.max(), density22.columns.max()))
n_tofs_max = np.max((density19.index.max(), density22.index.max()))
fig = make_subplots(
    rows=1, cols=2, subplot_titles=("pre-RET (Oct 2019)", "post-RET (Dec 2022)")
)
fig.add_trace(
    go.Heatmap(
        z=density19.values,
        x=density19.columns,
        y=density19.index,
        colorscale="reds",
        zmid=0,
        zmin=0,
        zmax=np.max((density19.max().max(), density22.max().max())),
        colorbar=dict(title="density"),
        hoverongaps=False,
        texttemplate="%{z:" + ".0e" + "}",
    ),
    row=1,
    col=1,
)
fig.add_trace(
    go.Heatmap(
        z=density22.values,
        x=density22.columns,
        y=density22.index,
        colorscale="reds",
        zmid=0,
        zmin=0,
        zmax=np.max((density19.max().max(), density22.max().max())),
        colorbar=dict(title="density"),
        hoverongaps=False,
        texttemplate="%{z:" + ".0e" + "}",
    ),
    row=1,
    col=2,
)
fig.update_layout(height=600, width=800)
# yaxis title = 'n_dep' and xaxis title = 'n_arr'
fig.update_yaxes(title_text="Number of departures per 15min intervals", row=1, col=1)
fig.update_xaxes(title_text="Number of arrivals per 15min intervals", row=1, col=1)
fig.update_yaxes(title_text="Number of departures per 15min intervals", row=1, col=2)
fig.update_xaxes(title_text="Number of arrivals per 15min intervals", row=1, col=2)
fig.update_layout(width=1000, height=500)
# keep ratio x and y to 1
# fig.update_layout(yaxis=dict(scaleanchor="x", scaleratio=1))
# I want both plots to have the same x and y axis range use the max value of density19 and density23

fig.update_xaxes(range=[-0.5, n_lnds_max + 0.5], row=1, col=1)
fig.update_yaxes(range=[-0.5, n_tofs_max + 0.5], row=1, col=1)
fig.update_xaxes(range=[-0.5, n_lnds_max + 0.5], row=1, col=2)
fig.update_yaxes(range=[-0.5, n_tofs_max + 0.5], row=1, col=2)

# make background transparent
fig.update_layout(plot_bgcolor="rgba(0,0,0,0)")

# make the grif lines black

## add tick values at all integer values

fig.update_xaxes(
    showgrid=True,
    ticks="outside",
    tickson="boundaries",
    tickvals=np.arange(0, n_lnds_max + 1),
    ticklen=3
)
fig.update_yaxes(
    showgrid=True,
    ticks="outside",
    tickson="boundaries",
    tickvals=np.arange(0, n_tofs_max + 1),
    ticklen=3
)
# add black line for x and y axis
fig.update_xaxes(showline=True, linewidth=1, linecolor="black")
fig.update_yaxes(showline=True, linewidth=1, linecolor="black")
# fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor="black")
fig.write_image("figures/density19vs22.pdf")

fig.show()